In [1]:
import numpy as np

import torch
from tqdm.autonotebook import tqdm

import os
import time
import logging
import re
#device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device = 'cpu'
print(device)

cpu


C:\Users\Mateo\AppData\Local\Temp\ipykernel_18612\3940245788.py:4: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm


In [2]:
from pathlib import Path

DATASET_PATH_TRAIN = Path("data/aclImdb/aclImdb/train")
DATASET_PATH_TEST = Path("data/aclImdb/aclImdb/test")

NB_DOC_MAX = 1000 # par classe
IMDB_CLASSES  = ['neg','pos']
VOC_SIZE = 10000
BATCH_SIZE = 32
MAX_CHAR_SIZE = 1000


labels = dict(zip(IMDB_CLASSES,[0,1]))

def load_data(datapath, classes, max_size=None):
    txts = []
    files = []
    filelabels = []
    for label in classes:
        c = 0
        new = [os.path.join(datapath / label, f) for f in os.listdir(datapath / label) if f.endswith(".txt")]
        files += new
        # filelabels += [labels[label]] * len(new) 
        for file in (datapath / label).glob("*.txt"):
            t = file.read_text(encoding='utf8')
            txts.append(t if len(t)<MAX_CHAR_SIZE else t[:MAX_CHAR_SIZE])
            filelabels.append(labels[label])
            c+=1
            if max_size !=None and c>=max_size: break

    return txts, files, filelabels
    #     c+=1
    #     if train_max_size !=None and c>train_max_size: break


txts, files, filelabels = load_data(DATASET_PATH_TRAIN, IMDB_CLASSES, max_size = NB_DOC_MAX)
txts_test, files_test, filelabels_test = load_data(DATASET_PATH_TEST, IMDB_CLASSES, max_size = NB_DOC_MAX)

In [3]:
#essais et appropriation des données
filelabels[1999]

1

In [4]:
import torch.nn as nn
import torch.optim as optim
from sklearn.feature_extraction.text import CountVectorizer

# Vectorisation avec BoW (fit sur les données d'entraînement uniquement)
vectorizer = CountVectorizer(max_features=1000)  # Limiter à 1000 mots pour simplifier
X_train = vectorizer.fit_transform(txts).toarray()
X_test = vectorizer.transform(txts_test).toarray()
vocab_size = X_train.shape[1]

print('vocab size : ', vocab_size)
print('X_train : ', X_train)

# Convertir les labels en tenseurs PyTorch
y_train = torch.tensor(filelabels, dtype=torch.long)
y_test = torch.tensor(filelabels_test, dtype=torch.long)

# Conversion des données en tenseurs PyTorch
X_train = torch.tensor(X_train, dtype=torch.float32)
X_test = torch.tensor(X_test, dtype=torch.float32)

# Définition du modèle
class BoWClassifier(nn.Module):
    def __init__(self, vocab_size, num_classes):
        super(BoWClassifier, self).__init__()
        self.fc = nn.Linear(vocab_size, num_classes)

    def forward(self, x):
        return self.fc(x)

# Initialisation du modèle
num_classes = 2  # Positif ou négatif
model = BoWClassifier(vocab_size, num_classes)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.01)

# Entraînement
num_epochs = 10
for epoch in range(num_epochs):
    model.train()
    optimizer.zero_grad()
    
    # Forward
    outputs = model(X_train)
    loss = criterion(outputs, y_train)
    
    # Backward
    loss.backward()
    optimizer.step()
    
    print(f"Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}")

# Évaluation
model.eval()
with torch.no_grad():
    outputs = model(X_test)
    _, predicted = torch.max(outputs, 1)
    accuracy = (predicted == y_test).sum().item() / y_test.size(0)
    print(f"Accuracy: {accuracy * 100:.2f}%")

vocab size :  1000
X_train :  [[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 1 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 1 0 0]]
Epoch [1/10], Loss: 0.7478
Epoch [2/10], Loss: 0.9195
Epoch [3/10], Loss: 0.6543
Epoch [4/10], Loss: 0.6197
Epoch [5/10], Loss: 0.6554
Epoch [6/10], Loss: 0.5692
Epoch [7/10], Loss: 0.4765
Epoch [8/10], Loss: 0.4639
Epoch [9/10], Loss: 0.4797
Epoch [10/10], Loss: 0.4576
Accuracy: 76.25%


In [5]:
import json
from collections import Counter


# Loading json
with open("./ressources/json_pol/json_pol",encoding="utf-8") as f:
    data = f.readlines()
    json_data = json.loads(data[0])
    train = json_data["train"]
    test = json_data["test"]
    

# Quick Check
counter_train = Counter((x[1] for x in train))
counter_test = Counter((x[1] for x in test))
print("Number of train reviews : ", len(train))
print("----> # of positive : ", counter_train[1])
print("----> # of negative : ", counter_train[0])
print("")
print(train[0])
print("")
print("Number of test reviews : ",len(test))
print("----> # of positive : ", counter_test[1])
print("----> # of negative : ", counter_test[0])

print("")
print(test[0])
print("")

Number of train reviews :  25000
----> # of positive :  12500
----> # of negative :  12500

["The undoubted highlight of this movie is Peter O'Toole's performance. In turn wildly comical and terribly terribly tragic. Does anybody do it better than O'Toole? I don't think so. What a great face that man has!<br /><br />The story is an odd one and quite disturbing and emotionally intense in parts (especially toward the end) but it is also oddly touching and does succeed on many levels. However, I felt the film basically revolved around Peter O'Toole's luminous performance and I'm sure I wouldn't have enjoyed it even half as much if he hadn't been in it.", 1]

Number of test reviews :  25000
----> # of positive :  12500
----> # of negative :  12500

['Although credit should have been given to Dr. Seuess for stealing the story-line of "Horton Hatches The Egg", this was a fine film. It touched both the emotions and the intellect. Due especially to the incredible performance of seven year old 

In [6]:
from sklearn.feature_extraction.text import CountVectorizer
classes = [pol for text,pol in train]
corpus = [text for text,pol in train]

vectorizer = CountVectorizer()

X = vectorizer.fit_transform(corpus)
print(vectorizer.get_feature_names_out()[:500]) # we only print a few
print(len(vectorizer.get_feature_names_out()))

['00' '000' '0000000000001' '00001' '00015' '000s' '001' '003830' '006'
 '007' '0079' '0080' '0083' '0093638' '00am' '00pm' '00s' '01' '01pm' '02'
 '020410' '029' '03' '04' '041' '05' '050' '06' '06th' '07' '08' '087'
 '089' '08th' '09' '0f' '0ne' '0r' '0s' '10' '100' '1000' '1000000'
 '10000000000000' '1000lb' '1000s' '1001' '100b' '100k' '100m' '100min'
 '100mph' '100s' '100th' '100x' '100yards' '101' '101st' '102' '102nd'
 '103' '104' '1040' '1040a' '1040s' '105' '1050' '105lbs' '106' '106min'
 '107' '108' '109' '10am' '10lines' '10mil' '10min' '10minutes' '10p'
 '10pm' '10s' '10star' '10th' '10x' '10yr' '11' '110' '1100' '11001001'
 '1100ad' '111' '112' '1138' '114' '1146' '115' '116' '117' '11f' '11m'
 '11th' '12' '120' '1200' '1200f' '1201' '1202' '123' '12383499143743701'
 '125' '125m' '127' '128' '12a' '12hr' '12m' '12mm' '12s' '12th' '13'
 '130' '1300' '1300s' '131' '1318' '132' '134' '135' '135m' '136' '137'
 '138' '139' '13k' '13s' '13th' '14' '140' '1408' '140hp' '1415' '14

In [7]:
from sklearn.naive_bayes import MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.svm import LinearSVC
from sklearn.metrics import accuracy_score


#Naïve Bayes
nb_clf = MultinomialNB()
nb_clf.fit(X, classes)


#Logistic Regression
lr_clf = LogisticRegression(random_state=0, solver='lbfgs',n_jobs=-1)
lr_clf.fit(X, classes)

#Linear SVM
svm_clf = LinearSVC(random_state=0, tol=1e-5)
svm_clf.fit(X, classes)


true = [pol for text,pol in test]
test_corpus = [text for text,pol in test]
X_test = vectorizer.transform(test_corpus)

pred_nb = nb_clf.predict(X_test)
pred_lr = lr_clf.predict(X_test)
pred_svm = svm_clf.predict(X_test)


print(f"Naïve Bayes accuracy: {accuracy_score(true, pred_nb)}")
print(f"Logistic Regression accuracy: {accuracy_score(true, pred_lr)}")
print(f"SVM accuracy: {accuracy_score(true, pred_svm)}")

C:\Users\Mateo\AppData\Local\miniconda3\envs\version_vguigue\Lib\site-packages\sklearn\svm\_base.py:1235: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(


Naïve Bayes accuracy: 0.81356
Logistic Regression accuracy: 0.86392
SVM accuracy: 0.84576


In [8]:
#passage au deep

from torch.utils.data import Dataset, DataLoader

GLOVE_PATH = Path("data/glove/glove")
DATASET_PATH = Path("data/aclImdb/aclImdb")
IMDB_CLASSES  = ['neg','pos']

class FolderText(Dataset):
    """Dataset basé sur des dossiers (un par classe) et fichiers"""

    def __init__(self, classes, folder: Path, tokenizer, train_max_size=None, load=False):
        self.tokenizer = tokenizer
        self.files = []
        self.filelabels = []
        self.labels = {key: ix for ix, key in enumerate(classes)}
        
        for label in classes:
            c = 0
            for file in (folder / label).glob("*.txt"):
                self.files.append(file.read_text(encoding='utf8') if load else file)
                self.filelabels.append(self.labels[label])
                c += 1
                if train_max_size is not None and c > train_max_size:
                    break

    def __len__(self):
        return len(self.filelabels)
    
    def __getitem__(self, ix):
        s = self.files[ix]
        tokenized = torch.tensor(self.tokenizer(s if isinstance(s, str) else s.read_text()), device=device)
        label = torch.tensor(self.filelabels[ix], device=device)
        return tokenized, label

def get_imdb_data(embedding_size=50, train_max_size=None):
    """Renvoie l'ensemble des données nécessaires pour l'apprentissage 

    - dictionnaire word vers ID
    - embeddings (Glove)
    - DataSet (FolderText)

    """
    WORDS = re.compile(r"\S+")
    glove_fn = open(GLOVE_PATH / ("glove.6B.%dd.txt" % embedding_size), encoding='utf8')
    words, embeddings = [], []
    
    for line in glove_fn:
        values = line.split()
        words.append(values[0])
        embeddings.append([float(x) for x in values[1:]])

    OOVID = len(words)
    words.append("__OOV__")

    word2id = {word: ix for ix, word in enumerate(words)}
    embeddings = np.vstack((embeddings, np.zeros(embedding_size)))
    embeddings = torch.tensor(embeddings, dtype=torch.float32, device=device)

    def tokenizer(t):
        return [word2id.get(x, OOVID) for x in re.findall(WORDS, t.lower())]

    logging.info("Loading embeddings")
    logging.info("Get the IMDB dataset")
    
    return word2id, embeddings, FolderText(IMDB_CLASSES, DATASET_PATH / "train", tokenizer, train_max_size, load=True), FolderText(IMDB_CLASSES, DATASET_PATH / "test", tokenizer, train_max_size, load=True)

In [9]:
word2id, embeddings, train_dataset, test_dataset = get_imdb_data()

In [10]:
# vérification des données chargées:

word2id
# embeddings
# train_dataset[0]

print(len(word2id), len(embeddings), len(embeddings[0]))


400001 400001 50


In [11]:
#data loader

from torch.nn.utils.rnn import pad_sequence

BATCH_SIZE = 100

def collate_fn(batch):
    sequences, labels = zip(*batch)
    lengths = torch.tensor([len(seq) for seq in sequences], device=device)
    padded_sequences = pad_sequence(sequences, batch_first=False).to(device)
    labels = torch.tensor(labels, device=device)
    return padded_sequences, torch.tensor(lengths), torch.tensor(labels)

train_loader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True,  collate_fn=collate_fn)
test_loader = DataLoader(test_dataset, batch_size=BATCH_SIZE, shuffle=False, collate_fn=collate_fn)

In [12]:
# Test

batch =next(iter( train_loader))
padded_sequences, lengths, labels = batch
print("Padded sequences:", padded_sequences)
print(padded_sequences.size())
# print("Lengths:", lengths)
print("Labels:", labels)



Padded sequences: tensor([[ 28051, 400000,    575,  ...,     19,    109,     37],
        [  6732,     41,     14,  ...,   1318,    249,     14],
        [    96, 400000, 400000,  ...,     38,     49,     36],
        ...,
        [     0,      0,      0,  ...,      0,      0,      0],
        [     0,      0,      0,  ...,      0,      0,      0],
        [     0,      0,      0,  ...,      0,      0,      0]])
torch.Size([575, 100])
Labels: tensor([0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 1, 1,
        0, 1, 1, 1, 0, 1, 1, 1, 1, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1,
        0, 0, 1, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0,
        0, 0, 0, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 0,
        1, 0, 0, 0])


C:\Users\Mateo\AppData\Local\Temp\ipykernel_18612\195418350.py:12: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  return padded_sequences, torch.tensor(lengths), torch.tensor(labels)


In [13]:
#réseau
import torch.nn.functional as F

import torch
import torch.nn as nn
import torch.nn.functional as F

class RNNSent(nn.Module):
    def __init__(self, hidden_size, output_size, embeddings, device):
        super(RNNSent, self).__init__()

        self.device = device
        self.hidden_size = hidden_size
        self.input_size = len(embeddings[0])

        self.emb = nn.Embedding(len(embeddings), len(embeddings[0]))

        # INITIALISATION des embeddings
        #self.emb.weight.data.copy_(torch.from_numpy(embeddings).to(device))
        self.emb.weight.requires_grad = False

        # CHOIX Du module récurrent
        self.rec = nn.RNN(self.input_size, self.hidden_size, nonlinearity='tanh').to(device)
        # self.rec = nn.LSTM(self.input_size, self.hidden_size).to(device)

        # ATTENTION
        self.attention = nn.Linear(hidden_size, 1, bias=False).to(device)

        self.h2o = nn.Linear(hidden_size, output_size).to(device)

    def forward(self, input, lengths=None):
        maxlen = input.size(0)
        batch_size = input.size(1)

        # Déplacer l'entrée sur le bon device
        input = input.to(self.device)
        if lengths is not None:
            lengths = lengths.to(self.device)

        # 1. translation of the input from int to emb
        xemb = self.emb(input).to(self.device)
        #print("xemb", xemb.size())

        # 2. Passage dans le rec
        hidden, last = self.rec(xemb)   # RNN
        # hidden, (last,c) = self.rec(xemb) # LSTM => last[-1]
        #print("hidden", hidden.size())

        # récupération des dernières couches (réelles, sans padding)
        if lengths is not None:
            last = torch.stack([hidden[lengths[i] - 1, i, :].to(self.device) for i in range(batch_size)])

        # 3. Ajout de l'attention (non nécessaire dans un premier temps)
        # 3.1 passage dans l'attention
        a = self.attention(hidden).squeeze(-1).to(self.device)
        #print(a.size())

        # 3.2 mask [à comprendre impérativement]
        mask = torch.arange(maxlen, device=self.device).unsqueeze(1).expand(maxlen, batch_size) < lengths.unsqueeze(0)
        #print(mask)
        masked_attn_scores = a.masked_fill(~mask, float('-inf'))

        # 3.3 calcul de l'attention (utilisation du softmax) + application sur les couches cachées
        a = F.softmax(masked_attn_scores, dim=0).unsqueeze(-1)
        #print("a", a.size())
        #print("hidden", hidden.size())

        last = torch.sum(a * hidden, dim=0)
        #print("last", last.size())

        output = self.h2o(last).squeeze(0)
        #output = self.h2o(last) # LSTM
        
        return output, hidden

In [14]:
# choose hidden size
n_hidden = 128
output_size = 2
# build network
rnn = RNNSent( n_hidden,  output_size, embeddings, device)
rnn.name = "RNNSent-"+time.asctime()

In [15]:
loss = nn.CrossEntropyLoss()
# batch
x, lengths, y = next(iter(train_loader))
print(x.size(),y.size())

# maxlen = x.size()[0]
# mask = torch.arange(maxlen).unsqueeze(1).expand(maxlen, 100) < lengths.unsqueeze(0)
# print(mask)
yhat, hidden = rnn(x, lengths)
print(yhat.size())
l = loss(yhat,y)

C:\Users\Mateo\AppData\Local\Temp\ipykernel_18612\195418350.py:12: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  return padded_sequences, torch.tensor(lengths), torch.tensor(labels)


torch.Size([992, 100]) torch.Size([100])
xemb torch.Size([992, 100, 50])
hidden torch.Size([992, 100, 128])
torch.Size([992, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]])
a torch.Size([992, 100, 1])
hidden torch.Size([992, 100, 128])
last torch.Size([100, 128])
torch.Size([100, 2])


In [16]:
# définition de la métrique d'évaluation
def accuracy(yhat,y):
    # y encode les indexes, s'assurer de la bonne taille de tenseur
    assert len(y.shape)==1 or y.size(1)==1
    return (torch.argmax(yhat,1).view(y.size(0),-1)== y.view(-1,1)).float().mean()

In [17]:
def train(model,epochs,train_loader,test_loader):
    optim = torch.optim.Adam(model.parameters(),lr=1e-3)    # choix optimizer
    model = model.to(device)
    print(f"running {model.name}")
    loss = nn.CrossEntropyLoss()                            # choix loss
    # 
    # loss = nn.CrossEntropyLoss(weight=cl_weight.to(device))                            # choix loss
    for epoch in tqdm(range(epochs)):
        cumloss, cumacc, count = 0, 0, 0
        model.train()
        for x, lengths, y in train_loader:                            # boucle sur les batchs
            optim.zero_grad()
            x,y = x.to(device), y.to(device)                # y doit être un tensor (pas un int)
            yhat, next_hidden = model(x, lengths)
            l = loss(yhat,y)
            l.backward()
            optim.step()
            cumloss += l*len(x)                             # attention, il peut y avoir un batch + petit (le dernier)
            cumacc += accuracy(yhat,y)*len(x)
            count += len(x)
        #writer.add_scalar('loss/train',cumloss/count,epoch)
        #writer.add_scalar('accuracy/train',cumacc/count,epoch)
        if epoch % 2 == 0:
            model.eval()
            with torch.no_grad():
                cumloss, cumacc, count = 0, 0, 0
                for x, lengths, y in test_loader:
                    x,y = x.to(device), y.to(device)
                    yhat, next_hidden = model(x, lengths)
                    cumloss += loss(yhat,y)*len(x)
                    cumacc += accuracy(yhat,y)*len(x)
                    count += len(x)
                #writer.add_scalar(f'loss/test',cumloss/count,epoch)
                #writer.add_scalar('accuracy/test',cumacc/count,epoch)

In [18]:
# ~10 minutes sur CPU
n_epoch = 20
train(rnn, n_epoch, train_loader, test_loader)

running RNNSent-Thu Feb  6 16:32:23 2025


  0%|          | 0/20 [00:00<?, ?it/s]

C:\Users\Mateo\AppData\Local\Temp\ipykernel_18612\195418350.py:12: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  return padded_sequences, torch.tensor(lengths), torch.tensor(labels)


xemb torch.Size([1001, 100, 50])
hidden torch.Size([1001, 100, 128])
torch.Size([1001, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]])
a torch.Size([1001, 100, 1])
hidden torch.Size([1001, 100, 128])
last torch.Size([100, 128])
xemb torch.Size([1057, 100, 50])
hidden torch.Size([1057, 100, 128])
torch.Size([1057, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]

xemb torch.Size([941, 100, 50])
hidden torch.Size([941, 100, 128])
torch.Size([941, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]])
a torch.Size([941, 100, 1])
hidden torch.Size([941, 100, 128])
last torch.Size([100, 128])
xemb torch.Size([997, 100, 50])
hidden torch.Size([997, 100, 128])
torch.Size([997, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False,  True, False],
        [False, False, False,  ..., False,  True, False],
        [False, False, False,  ..., False,  True, False]])
a tor

...

xemb torch.Size([811, 100, 50])
hidden torch.Size([811, 100, 128])
torch.Size([811, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]])
a torch.Size([811, 100, 1])
hidden torch.Size([811, 100, 128])
last torch.Size([100, 128])
xemb torch.Size([808, 100, 50])
hidden torch.Size([808, 100, 128])
torch.Size([808, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]])
a tor

xemb torch.Size([716, 100, 50])
hidden torch.Size([716, 100, 128])
torch.Size([716, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False,  True, False],
        [False, False, False,  ..., False,  True, False],
        [False, False, False,  ..., False,  True, False]])
a torch.Size([716, 100, 1])
hidden torch.Size([716, 100, 128])
last torch.Size([100, 128])
xemb torch.Size([918, 100, 50])
hidden torch.Size([918, 100, 128])
torch.Size([918, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]])
a tor

xemb torch.Size([986, 100, 50])
hidden torch.Size([986, 100, 128])
torch.Size([986, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]])
a torch.Size([986, 100, 1])
hidden torch.Size([986, 100, 128])
last torch.Size([100, 128])
xemb torch.Size([968, 100, 50])
hidden torch.Size([968, 100, 128])
torch.Size([968, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]])
a tor

xemb torch.Size([885, 100, 50])
hidden torch.Size([885, 100, 128])
torch.Size([885, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]])
a torch.Size([885, 100, 1])
hidden torch.Size([885, 100, 128])
last torch.Size([100, 128])
xemb torch.Size([974, 100, 50])
hidden torch.Size([974, 100, 128])
torch.Size([974, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]])
a tor

xemb torch.Size([968, 100, 50])
hidden torch.Size([968, 100, 128])
torch.Size([968, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]])
a torch.Size([968, 100, 1])
hidden torch.Size([968, 100, 128])
last torch.Size([100, 128])
xemb torch.Size([1001, 100, 50])
hidden torch.Size([1001, 100, 128])
torch.Size([1001, 100])
tensor([[ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        [ True,  True,  True,  ...,  True,  True,  True],
        ...,
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False, False]])
a 